<a href="https://colab.research.google.com/github/cabamarcos/SuperMask/blob/main/torch.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import torch
import torch.nn as nn
import torch.optim as optim
import torch.nn.functional as F
from torchvision import datasets, transforms
from torch.utils.data import DataLoader


import numpy as np
import matplotlib.pyplot as plt
import copy
from ast import Param

In [ ]:
# Verificar si la GPU está disponible y establecer el dispositivo
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

Using device: cpu


In [ ]:
class Net(nn.Module):
    def __init__(self):
        super(Net, self).__init__()
        self.fc1 = nn.Linear(784, 256)
        self.fc2 = nn.Linear(256, 128)
        self.fc3 = nn.Linear(128, 10)

    def forward(self, x):
        x = x.view(x.size(0), -1)
        x = F.relu(self.fc1(x))
        x = F.relu(self.fc2(x))
        x = self.fc3(x)
        return x


net = Net().to(device)

Definimos una red y le copiamos los pesos en una lista

In [ ]:
varianzas = Net().to(device)

varianzas_weights = []
for param in varianzas.parameters():
    varianzas_weights.extend(param.data.clone().flatten().tolist())
print(varianzas.state_dict())


OrderedDict([('fc1.weight', tensor([[ 0.0321,  0.0131, -0.0262,  ..., -0.0094,  0.0074, -0.0174],
        [-0.0275, -0.0341, -0.0249,  ..., -0.0138,  0.0313,  0.0023],
        [ 0.0163,  0.0098, -0.0097,  ...,  0.0301, -0.0108,  0.0092],
        ...,
        [-0.0115, -0.0355,  0.0101,  ...,  0.0085,  0.0026,  0.0156],
        [ 0.0017, -0.0084,  0.0112,  ...,  0.0202,  0.0212, -0.0041],
        [-0.0035,  0.0102, -0.0316,  ...,  0.0004, -0.0162,  0.0260]])), ('fc1.bias', tensor([ 0.0171,  0.0309, -0.0178,  0.0118,  0.0226,  0.0073,  0.0313, -0.0021,
        -0.0231, -0.0259,  0.0171,  0.0196,  0.0331, -0.0129,  0.0316,  0.0330,
        -0.0074, -0.0316,  0.0227,  0.0229, -0.0088,  0.0109, -0.0189, -0.0256,
        -0.0276, -0.0151,  0.0080,  0.0036, -0.0014,  0.0227, -0.0280,  0.0096,
        -0.0135,  0.0156, -0.0122,  0.0054, -0.0315,  0.0213,  0.0039, -0.0238,
        -0.0298, -0.0167, -0.0008,  0.0042, -0.0258, -0.0011, -0.0216, -0.0068,
         0.0129, -0.0005,  0.0076, -0.0185,

In [ ]:
print(varianzas_weights)

[0.03209201246500015, 0.013050330802798271, -0.026231367141008377, -0.010645637288689613, -0.023548923432826996, 0.021401312202215195, -0.012372097931802273, -0.015969282016158104, -0.03319208696484566, 0.02937185950577259, -0.00947658997029066, 0.022053642198443413, -0.02141323871910572, -0.02462904527783394, -0.019271783530712128, -0.002258752239868045, 0.030562495812773705, 0.03044852800667286, -0.02233283594250679, -0.013627828098833561, 0.02747105062007904, 0.006044707261025906, -0.0021679785568267107, 0.0034301963169127703, -0.006845810916274786, -0.008422741666436195, -0.007111132610589266, -0.02267950400710106, -0.017811227589845657, 0.020193427801132202, 0.0223175548017025, -0.014501925557851791, 0.004443279467523098, -0.008986588567495346, 0.0234810970723629, 0.0039732800796628, 0.016539787873625755, 0.01606968604028225, -0.026467937976121902, -0.033815521746873856, -0.033039577305316925, 0.005583533551543951, 0.014714667573571205, 0.009444726631045341, 0.02684905007481575, -

Cargamos los datos

In [ ]:
# Definimos el transform para los datos de MNIST
transform = transforms.Compose([
    transforms.ToTensor(),
    transforms.Normalize((0.1307,), (0.3081,))
])

# Cargamos el dataset de MNIST
train_dataset = datasets.MNIST('./data', train=True, download=True, transform=transform)
test_dataset = datasets.MNIST('./data', train=False, download=True, transform=transform)

# Definimos los DataLoaders para los conjuntos de entrenamiento y prueba
train_loader = DataLoader(train_dataset, batch_size=64, shuffle=True)
test_loader = DataLoader(test_dataset, batch_size=1000, shuffle=False)

In [ ]:
# Definimos la función de pérdida y los optimizadores
criterion = nn.CrossEntropyLoss()
optimizer = optim.SGD(net.parameters(), lr=0.01, momentum=0.9)

In [ ]:
def prune_weights(net):
    """This function prunes the 70% of the lowest weights in each layer of the network and sets them to zero"""
    for name, module in net.named_modules():
        if isinstance(module, nn.Linear):
            weights = module.weight.data.cpu().numpy()
            threshold = np.percentile(np.abs(weights), 70)
            weights[np.abs(weights) < threshold] = 0
            module.weight.data = torch.from_numpy(weights).to(device)
    return net